In [1]:
import yfinance as yf
from pyfinviz.screener import Screener
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from Utils import get_tickers
from window_time_utils import *
#import get_tickers
import scipy as sc
import sympy as sp
import copy
from statsmodels.tsa.seasonal import seasonal_decompose

from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
import os

from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split

from itertools import product,combinations

In [2]:
class model_searcher(object):
    def __init__(self,rank_size):
        self.rank={}
        for i in range(rank_size):
            self.rank[i]={"test_score":0,
                         "target_ticker":None}
        
    def model_search(self,data,Model_type,model_setting_dir,window,target_ticker,C):
        X,Y=past_data_prep(data,window,target_ticker=target_ticker)
        X_train, X_test, Y_train, Y_test = train_test_split(X, Y>0, test_size=0.33,shuffle=False)
        clf=make_pipeline(StandardScaler(),SVC(kernel="linear",C=C))
        clf.fit(X_train,Y_train)
        tr_sc=clf.score(X_train,Y_train)
        te_sc=clf.score(X_test,Y_test)
        results={
        "Model_type":Model_type,
        "train_score":tr_sc,
        "test_score":te_sc,
        "window":window,
        "target_ticker":target_ticker,
        "input_tickers":list(data["Close"].keys()),
        "C":C
        }
        top_scores=np.vectorize(lambda r:self.rank[r]["test_score"])(np.array(list(self.rank)))
        
        for i in range(len(top_scores)):
            if top_scores[i]<results["test_score"]:
                bt=np.vectorize(lambda k:self.rank[k]["target_ticker"])(list(self.rank.keys()))
                if not (results["target_ticker"] == bt[:(i)]).any():
                    self.rank[i]=results
                
                break
                
        np.save(model_setting_dir,self.rank)

    def model_search_fs(self,data,Model_type,model_setting_dir,window,target_ticker,C,feature_tickers):
        
        tickers=np.array(list(data["Close"].keys()))
        feature_tickers.append(target_ticker)
        sel_tickers=np.unique(np.array(feature_tickers))
        conditions=np.array(['Adj Close', 'Close', 'High', 'Low', 'Open', 'Volume'])
        data=data[list(product(*[conditions,sel_tickers.tolist()]))]
        
        X,Y=past_data_prep(data,window,target_ticker=target_ticker)
        X_train, X_test, Y_train, Y_test = train_test_split(X, Y>0, test_size=0.33,shuffle=False)
        clf=make_pipeline(StandardScaler(),SVC(kernel="linear",C=C))
        clf.fit(X_train,Y_train)
        tr_sc=clf.score(X_train,Y_train)
        te_sc=clf.score(X_test,Y_test)
        results={
        "Model_type":Model_type,
        "train_score":tr_sc,
        "test_score":te_sc,
        "window":window,
        "target_ticker":target_ticker,
        "input_tickers":sel_tickers.tolist(),
        "C":C
        }
        top_scores=np.vectorize(lambda r:self.rank[r]["test_score"])(np.array(list(self.rank)))
        
        for i in range(len(top_scores)):
            if top_scores[i]<results["test_score"]:
                bt=np.vectorize(lambda k:self.rank[k]["target_ticker"])(list(self.rank.keys()))
                if not (results["target_ticker"] == bt[:(i)]).any():
                    self.rank[i]=results
                
                break
                
        np.save(model_setting_dir,self.rank)

In [2]:
Tlist=get_tickers(page=3,vectorized=True,options=[Screener.SectorOption.BASIC_MATERIALS,Screener.IndexOption.SANDP_500])
Tlist=np.unique(np.array(Tlist)).tolist()
#data = yf.download(Tlist[:], period = "5y",interval = "1d")
#DEBUG
data = yf.download(Tlist[:], period = "2y",interval = "1h")
data

[*********************100%***********************]  21 of 21 completed


Adj Close                                     \
                                  ALB         APD          CE         CF   
2020-09-23 09:30:00-04:00         NaN         NaN         NaN        NaN   
2020-09-24 09:30:00-04:00   81.910004  287.950012  105.459999  30.299999   
2020-09-24 10:30:00-04:00   82.730003  288.459991  104.820702  30.340000   
2020-09-24 11:30:00-04:00   83.445000  289.750000  105.839996  30.760000   
2020-09-24 12:30:00-04:00   84.980003  291.494995  107.050003  31.045000   
...                               ...         ...         ...        ...   
2022-09-23 12:30:00-04:00  264.829987  234.315002   90.209999  93.379997   
2022-09-23 13:30:00-04:00  265.690002  234.630005   89.919998  93.455002   
2022-09-23 14:30:00-04:00  267.309998  235.580002   90.544998  93.660004   
2022-09-23 15:30:00-04:00  269.459991  237.169998   91.000000  93.830002   
2022-09-23 16:00:00-04:00  269.450012  237.070007   91.000000  93.790001   

                                                                        \
                                CTVA         DD        DOW         ECL   
2020-09-23 09:30:00-04:00        NaN        NaN        NaN         NaN   
2020-09-24 09:30:00-04:00  27.500000  54.189999  46.099998  194.265900   
2020-09-24 10:30:00-04:00  27.349899  53.860001  46.080002  193.339996   
2020-09-24 11:30:00-04:00  27.549999  54.340000  46.450001  195.279999   
2020-09-24 12:30:00-04:00  27.850000  54.855000  46.840000  197.044998   
...                              ...        ...        ...         ...   
2022-09-23 12:30:00-04:00  57.310001  50.000000  43.417599  147.990005   
2022-09-23 13:30:00-04:00  57.360001  50.115002  43.352001  147.539993   
2022-09-23 14:30:00-04:00  57.680000  50.380001  43.615002  148.500000   
2022-09-23 15:30:00-04:00  57.930000  50.770000  43.900002  149.289993   
2022-09-23 16:00:00-04:00  57.919998  50.740002  43.900002  149.259995   

                                                 ...    Volume            \
                                 EMN        FCX  ...       IFF       LIN   
2020-09-23 09:30:00-04:00        NaN        NaN  ...       NaN       NaN   
2020-09-24 09:30:00-04:00  76.680000  15.040000  ...  156137.0  214099.0   
2020-09-24 10:30:00-04:00  76.199997  15.105000  ...  110887.0  171304.0   
2020-09-24 11:30:00-04:00  77.029999  15.355000  ...   58282.0   94745.0   
2020-09-24 12:30:00-04:00  77.529999  15.505000  ...   57119.0   87418.0   
...                              ...        ...  ...       ...       ...   
2022-09-23 12:30:00-04:00  71.230003  26.361700  ...  138059.0  121694.0   
2022-09-23 13:30:00-04:00  71.279999  26.280001  ...  147788.0  233141.0   
2022-09-23 14:30:00-04:00  71.900002  26.415001  ...  142333.0  274248.0   
2022-09-23 15:30:00-04:00  72.699997  26.680000  ...  433077.0  235753.0   
2022-09-23 16:00:00-04:00  72.690002  26.680000  ...       0.0       0.0   

                                                                              \
                                LYB       MLM       MOS        NEM       NUE   
2020-09-23 09:30:00-04:00       NaN       NaN       NaN        NaN       NaN   
2020-09-24 09:30:00-04:00       0.0       0.0  974963.0  1588688.0  327679.0   
2020-09-24 10:30:00-04:00  444630.0   74460.0  393534.0   811971.0  115089.0   
2020-09-24 11:30:00-04:00  290601.0   48072.0  556537.0   665794.0  112331.0   
2020-09-24 12:30:00-04:00  221414.0   50982.0  775370.0   472669.0  166739.0   
...                             ...       ...       ...        ...       ...   
2022-09-23 12:30:00-04:00  338009.0   29486.0  824729.0   724180.0  141438.0   
2022-09-23 13:30:00-04:00  303296.0   50568.0  761998.0  1051093.0  179190.0   
2022-09-23 14:30:00-04:00  362802.0   60627.0  665142.0  1119960.0  199762.0   
2022-09-23 15:30:00-04:00  410364.0  116370.0  843422.0  2029203.0  358122.0   
2022-09-23 16:00:00-04:00       0.0       0.0       0.0        0.0       0.0   

                                              

In [4]:
Tlist=Tlist[:7]
combs=[]
for n in range(1,len(Tlist)+1):
    #combs.append(list(combinations(Tlist,n)))
    combs=combs + (list(combinations(Tlist,n)))
combs=np.vectorize(lambda c:list(c),otypes=[object])(np.array(combs)).tolist()    

C_list=list(np.arange(0.01,15.0,1.0))
window_list=list(np.arange(1,5))

<ipython-input-4-bbf83530c95d>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  combs=np.vectorize(lambda c:list(c),otypes=[object])(np.array(combs)).tolist()


In [5]:
params=list(product(*[
    window_list,
    Tlist ,
    C_list,
    combs
]))
len(params)

53340

In [6]:
MS=model_searcher(50)

MODEL RE-TRAIN

In [34]:
#Keep fixed
#Tickers

#Search in

#C
#Window size

C_list=list(np.arange(0.01,25.0,0.01))
window_list=list(np.arange(2,15))

In [3]:
from Investors import *

In [4]:
inv=SVC_investor(
        trade_freq=timedelta(minutes=60),
        model_description_dir="../Results/SVC_HOURS/Meta_SVC.npy",
        estimation_results_directory="../Results/SVC_HOURS/Running_results",
        market_availability=[time(hour=8,minute=15,second=0),time(hour=15,minute=5,second=0)],
        API_KEY="PKE3DH2LZD3W75TOI95M",
        secret_KEY="iWdYAw2IX9VfB7fJvB2djlDHHNY8sUMtTHxtW3lk"
    )

In [19]:
from joblib import load
from itertools import product
model=load(inv.model_description["model_state_params"]["model_state"])
model

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('svc', SVC(C=23, kernel='linear'))])

In [9]:
inv.model_description

{'model_state_params': {'model_state': '../Results/SVC_HOURS/SVC_MOS.joblib',
  'window': 3,
  'feature': 'Open',
  'options': [<SectorOption.BASIC_MATERIALS: 'sec_basicmaterials'>,
   <IndexOption.SANDP_500: 'idx_sp500'>],
  'interval': '1h',
  'period': '2d'},
 'start': '2021-08-27 09:30:00-04:00',
 'end': '2022-08-26 16:00:00-04:00',
 'Ticker': 'MOS',
 'Validation_period': '1y'}

In [33]:
tunning=list(product(*[C_list,window_list]))
tr_scs=[]
ts_scs=[]
for c,W in tunning:
    X,Y=past_data_prep(data,W,target_ticker=inv.model_description["Ticker"])
    X_train, X_test, Y_train, Y_test = train_test_split(X, Y>0, test_size=0.33,shuffle=False)
    clf=make_pipeline(StandardScaler(),SVC(kernel="linear",C=c))
    clf.fit(X_train,Y_train)
    tr_sc=clf.score(X_train,Y_train)
    te_sc=clf.score(X_test,Y_test)
    print(c)
    print(W)
    print(tr_sc)
    print(te_sc)
    tr_scs.append(tr_sc)
    ts_scs.append(ts_sc)

0.01
2
0.6011904761904762
0.5137931034482759
0.01
3
0.6187234042553191
0.5120689655172413
0.01
4
0.6340425531914894
0.5112262521588946


C:\Users\grmc1\Anaconda3\envs\trading\lib\site-packages\pandas\core\frame.py:3678: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self[col] = igetitem(value, i)


0.01
5
0.637137989778535
0.5112262521588946


C:\Users\grmc1\Anaconda3\envs\trading\lib\site-packages\pandas\core\frame.py:3678: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self[col] = igetitem(value, i)


0.01
6
0.6445012787723785
0.5094991364421416


...

24.01
12
0.9555175363558597
0.8093587521663779


C:\Users\grmc1\Anaconda3\envs\trading\lib\site-packages\pandas\core\frame.py:3678: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self[col] = igetitem(value, i)


24.01
13
0.9597946963216424
0.8350694444444444


C:\Users\grmc1\Anaconda3\envs\trading\lib\site-packages\pandas\core\frame.py:3678: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self[col] = igetitem(value, i)


24.01
14
0.9631849315068494
0.8246527777777778


In [ ]:
test_list,train_list=inv.new_model_search(data)

0.01
2
0.5573491928632116
0.5793103448275863
0.01
3
0.621334466638334
0.5982758620689655
0.01
4
0.6404589885252868
0.5746333045729077


C:\Users\grmc1\Anaconda3\envs\trading\lib\site-packages\pandas\core\frame.py:3678: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self[col] = igetitem(value, i)


0.01
5
0.64328231292517
0.5565142364106989


C:\Users\grmc1\Anaconda3\envs\trading\lib\site-packages\pandas\core\frame.py:3678: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self[col] = igetitem(value, i)


0.01
6
0.6363249680986814
0.5418464193270061


...

C:\Users\grmc1\Anaconda3\envs\trading\lib\site-packages\pandas\core\frame.py:3678: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self[col] = igetitem(value, i)


6.174999999999999
10
0.9323116219667944
0.8954191875540191


C:\Users\grmc1\Anaconda3\envs\trading\lib\site-packages\pandas\core\frame.py:3678: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self[col] = igetitem(value, i)


6.174999999999999
11
0.9327086882453152
0.8928262748487468


C:\Users\grmc1\Anaconda3\envs\trading\lib\site-packages\pandas\core\frame.py:3678: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self[col] = igetitem(value, i)
